In [5]:
entities_list = [
        # {
        #     "chebi_chemical_entities": {
        #         "uri": "http://purl.obolibrary.org/obo/CHEBI",
        #         "label": "chemical entities",
        #         "description": "Chemical entities in ChEBI.",
        #         "endpoint": "https://sparql.uniprot.org/sparql/",
        #         "pagination": True,
        #         "query": """
        #                 PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
        #                 PREFIX rh:   <http://rdf.rhea-db.org/>
        #                 SELECT DISTINCT ?uri ?label
        #                 WHERE {
        #                     # Restrict to things that are recognized as Rhea reactions
        #                     ?reaction rdfs:subClassOf rh:Reaction ;
        #                             rh:side        ?side .
        #                     # Each reaction side contains one or more participants
        #                     ?side rh:contains ?participant .
        #                     # Each participant is linked to a ChEBI entity via 'rh:compound' 
        #                     ?participant rh:compound ?compound .
        #                     # 'rh:chebi' points to the ChEBI identifier (e.g., http://purl.obolibrary.org/obo/CHEBI_15377)
        #                     ?compound rh:chebi ?uri .
        #                     ?uri rdfs:label ?label .
        #                 }"""
        #     }
        # },
        # {
        #     "uniprot_disease": {
        #         "uri": "http://purl.uniprot.org/core/Disease",
        #         "label": "Disease",
        #         "description": "The preferred names of diseases.",
        #         "endpoint": "https://sparql.uniprot.org/sparql/",
        #         "pagination": True,
        #         "query": """PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
        #                     PREFIX skos: <http://www.w3.org/2004/02/skos/core#>
        #                     PREFIX up: <http://purl.uniprot.org/core/>
        #                     SELECT ?uri ?label ?type WHERE {
        #                         ?uri a up:Disease ;
        #                             skos:prefLabel ?label .
        #                     }"""
        #     }
        # },
        {
            "uniprot_taxon": {
                "uri": "http://purl.uniprot.org/core/Taxon",
                "label": "species",
                "description": "taxon scientific names",
                "endpoint": "https://sparql.uniprot.org/sparql/",
                "pagination": True,
                "query": """PREFIX up: <http://purl.uniprot.org/core/>
                            SELECT ?uri ?label
                            WHERE {
                                ?uri a up:Taxon ;
                                    up:scientificName ?label .
                            }"""
            }
        },
        # {
        #     "rhea_reaction": {
        #         "uri": "http://rdf.rhea-db.org/",
        #         "label": "reactions",
        #         "description": "Reactions in RHEA.",
        #         "endpoint": "https://sparql.uniprot.org/sparql/",
        #         "pagination": True,
        #         "query": """PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
        #                     PREFIX rh:   <http://rdf.rhea-db.org/>
        #                     SELECT DISTINCT ?uri ?label
        #                     WHERE {
        #                         ?uri rdfs:subClassOf rh:Reaction .
        #                         ?uri rdfs:label ?label .
        #                     }"""
        #     }
        # },
        
    ]

In [6]:
from endpoint_loader import *
import pandas as pd
entities = load_entities_from_endpoints(entities_list)

df = pd.DataFrame(entities)

display(df.head())

print(f"Total entities: {len(df)}")
print(f"Columns: {df.columns.tolist()}")
print(f"Entity types: {df['entity_type'].unique()}")

Flattened 1 entities for indexing
Flattened entities: [{'uri': 'http://purl.uniprot.org/core/Taxon', 'label': 'species', 'description': 'taxon scientific names', 'endpoint': 'https://sparql.uniprot.org/sparql/', 'pagination': True, 'query': 'PREFIX up: <http://purl.uniprot.org/core/>\n                            SELECT ?uri ?label\n                            WHERE {\n                                ?uri a up:Taxon ;\n                                    up:scientificName ?label .\n                            }'}]
Loading entities from https://sparql.uniprot.org/sparql/ for species...
Found 200000 entities for species in https://sparql.uniprot.org/sparql/
  Retrieved 200000 entities, total so far: 200000
Found 200000 entities for species in https://sparql.uniprot.org/sparql/
  Retrieved 200000 entities, total so far: 400000
Found 200000 entities for species in https://sparql.uniprot.org/sparql/
  Retrieved 200000 entities, total so far: 600000
Found 200000 entities for species in https:

label                                      uri  \
0     Hysteriaceae  http://purl.uniprot.org/taxonomy/100025   
1         Thomomys   http://purl.uniprot.org/taxonomy/10011   
2  Thomomys bottae   http://purl.uniprot.org/taxonomy/10013   
3     Heteromyidae   http://purl.uniprot.org/taxonomy/10015   
4     Philenoptera  http://purl.uniprot.org/taxonomy/100163   

                         endpoint_url entity_type             description  
0  https://sparql.uniprot.org/sparql/     literal  taxon scientific names  
1  https://sparql.uniprot.org/sparql/     literal  taxon scientific names  
2  https://sparql.uniprot.org/sparql/     literal  taxon scientific names  
3  https://sparql.uniprot.org/sparql/     literal  taxon scientific names  
4  https://sparql.uniprot.org/sparql/     literal  taxon scientific names

Total entities: 2614312
Columns: ['label', 'uri', 'endpoint_url', 'entity_type', 'description']
Entity types: ['literal']


In [3]:
import pickle

df.to_csv('entities_dataframe.csv', index=False)  
with open('entities_dataframe.pkl', 'wb') as f:
    pickle.dump(df, f)

In [2]:
import os
import pickle
if os.path.exists('entities_dataframe.pkl'):
    with open('entities_dataframe.pkl', 'rb') as f:
        df = pickle.load(f)
        entities = df.to_dict('records')
else:
    # Load from endpoint if file doesn't exist
    from endpoint_loader import *
    entities = load_entities_from_endpoints(entities_list)
    df = pd.DataFrame(entities)
    # Save for next time
    with open('entities_data.pkl', 'wb') as f:
        pickle.dump(df, f)

In [ ]:
from entity_indexing_pipeline_v3 import EmbeddingPipeline
import ray


ray.init(ignore_reinit_error=True)
s
pipeline = EmbeddingPipeline()
pipeline.add_documents(entities, batch_size=144)

ray.shutdown()

2025-03-29 10:39:10,837	INFO worker.py:1843 -- Started a local Ray instance. View the dashboard at http://127.0.0.1:8265 


Creating embedding workers...
Initializing Qdrant client...


Fetching 5 files:   0%|          | 0/5 [00:00<?, ?it/s]

tokenizer.json:   0%|          | 0.00/711k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/695 [00:00<?, ?B/s]

...

tokenizer_config.json:   0%|          | 0.00/1.38k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/712k [00:00<?, ?B/s]

Error loading upload log: Expecting ',' delimiter: line 1 column 19775128 (char 19775127)
Collection 'biomedical_entities' exists, skipping initialization
Adding 2650724 documents in batches of 144
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 3.075160026550293 seconds
Time taken to generate sparse embeddings with Ray Distributed Computing: 13.96476697921753 seconds
Creating points...
Uploading points...
✓ Batch 1/18408 - Total uploaded: 144
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 3.969425916671753 seconds
Time taken to generate sparse embeddings with Ray Distributed Computing: 22.855857133865356 seconds
Creating points...
Uploading points...
✓ Batch 2/18408 - Total uploaded: 288
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 3.8981409072875977 seconds
Time taken to generate sparse embeddings with Ray Distributed Computing: 23.256271839141846 seconds
Creating 

Exception ignored in: <bound method IPythonKernel._clean_thread_parent_frames of <ipykernel.ipkernel.IPythonKernel object at 0x103114790>>
Traceback (most recent call last):
  File "/Users/sebastian/Documents/Bachelor Thesis/sparql-rag-agent/sparql-rag-agent/.venv/lib/python3.11/site-packages/ipykernel/ipkernel.py", line 775, in _clean_thread_parent_frames
    def _clean_thread_parent_frames(

KeyboardInterrupt: 


Time taken to generate sparse embeddings with Ray Distributed Computing: 8.83504581451416 seconds
Creating points...
Uploading points...
✓ Batch 7/18408 - Total uploaded: 1008
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 4.275254964828491 seconds


In [5]:
ray.shutdown()

In [2]:
entities_list = [
        {
            "chebi_chemical_entities": {
                "uri": "http://purl.obolibrary.org/obo/CHEBI",
                "label": "chemical entities",
                "description": "Chemical entities in ChEBI.",
                "endpoint": "https://sparql.uniprot.org/sparql/",
                "pagination": True,
                "query": """
                        PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
                        PREFIX rh:   <http://rdf.rhea-db.org/>
                        SELECT DISTINCT ?uri ?label
                        WHERE {
                            # Restrict to things that are recognized as Rhea reactions
                            ?reaction rdfs:subClassOf rh:Reaction ;
                                    rh:side        ?side .
                            # Each reaction side contains one or more participants
                            ?side rh:contains ?participant .
                            # Each participant is linked to a ChEBI entity via 'rh:compound' 
                            ?participant rh:compound ?compound .
                            # 'rh:chebi' points to the ChEBI identifier (e.g., http://purl.obolibrary.org/obo/CHEBI_15377)
                            ?compound rh:chebi ?uri .
                            ?uri rdfs:label ?label .
                        }"""
            }
        },
        {
            "uniprot_disease": {
                "uri": "http://purl.uniprot.org/core/Disease",
                "label": "Disease",
                "description": "The preferred names of diseases.",
                "endpoint": "https://sparql.uniprot.org/sparql/",
                "pagination": True,
                "query": """PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
                            PREFIX skos: <http://www.w3.org/2004/02/skos/core#>
                            PREFIX up: <http://purl.uniprot.org/core/>
                            SELECT ?uri ?label ?type WHERE {
                                ?uri a up:Disease ;
                                    skos:prefLabel ?label .
                            }"""
            }
        },
        {
            "uniprot_taxon": {
                "uri": "http://purl.uniprot.org/core/Taxon",
                "label": "species",
                "description": "taxon scientific names",
                "endpoint": "https://sparql.uniprot.org/sparql/",
                "pagination": True,
                "query": """PREFIX up: <http://purl.uniprot.org/core/>
                            SELECT ?uri ?label
                            WHERE {
                                ?uri a up:Taxon ;
                                    up:scientificName ?label .
                            }"""
            }
        },
        {
            "rhea_reaction": {
                "uri": "http://rdf.rhea-db.org/",
                "label": "reactions",
                "description": "Reactions in RHEA.",
                "endpoint": "https://sparql.uniprot.org/sparql/",
                "pagination": True,
                "query": """PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>
                            PREFIX rh:   <http://rdf.rhea-db.org/>
                            SELECT DISTINCT ?uri ?label
                            WHERE {
                                ?uri rdfs:subClassOf rh:Reaction .
                                ?uri rdfs:label ?label .
                            }"""
            }
        },
        
    ]

In [3]:
from endpoint_loader import *
import pandas as pd
entities = load_entities_from_endpoints(entities_list)

df = pd.DataFrame(entities)

display(df.head())
print(f"Total entities: {len(df)}")
print(f"Columns: {df.columns.tolist()}")
print(f"Entity types: {df['entity_type'].unique()}")

Flattened 4 entities for indexing
Flattened entities: [{'uri': 'http://purl.obolibrary.org/obo/CHEBI', 'label': 'chemical entities', 'description': 'Chemical entities in ChEBI.', 'endpoint': 'https://sparql.uniprot.org/sparql/', 'pagination': True, 'query': "\n                        PREFIX rdfs: <http://www.w3.org/2000/01/rdf-schema#>\n                        PREFIX rh:   <http://rdf.rhea-db.org/>\n                        SELECT DISTINCT ?uri ?label\n                        WHERE {\n                            # Restrict to things that are recognized as Rhea reactions\n                            ?reaction rdfs:subClassOf rh:Reaction ;\n                                    rh:side        ?side .\n                            # Each reaction side contains one or more participants\n                            ?side rh:contains ?participant .\n                            # Each participant is linked to a ChEBI entity via 'rh:compound' \n                            ?participant rh:compound 

label  \
0  2-O-(alpha-D-mannopyranosyl)-1-phosphatidyl-1D...   
1                   (3E,5Z)-tetradecadienoyl-CoA(4-)   
2                         (5Z)-tetradecenoyl-CoA(4-)   
3        (25R)-3beta-hydroxycholest-5-en-7-one-26-al   
4      (25R)-3beta-hydroxycholest-5-en-7-one-26-oate   

                                          uri  \
0  http://purl.obolibrary.org/obo/CHEBI_87673   
1  http://purl.obolibrary.org/obo/CHEBI_71586   
2  http://purl.obolibrary.org/obo/CHEBI_84650   
3  http://purl.obolibrary.org/obo/CHEBI_87677   
4  http://purl.obolibrary.org/obo/CHEBI_87678   

                         endpoint_url entity_type                  description  
0  https://sparql.uniprot.org/sparql/     literal  Chemical entities in ChEBI.  
1  https://sparql.uniprot.org/sparql/     literal  Chemical entities in ChEBI.  
2  https://sparql.uniprot.org/sparql/     literal  Chemical entities in ChEBI.  
3  https://sparql.uniprot.org/sparql/     literal  Chemical entities in ChEBI.  
4  https://sparql.uniprot.org/sparql/     literal  Chemical entities in ChEBI.

Total entities: 2650724
Columns: ['label', 'uri', 'endpoint_url', 'entity_type', 'description']
Entity types: ['literal']


In [4]:
from entity_indexing_pipeline_v3 import EmbeddingPipeline
import ray


ray.init(ignore_reinit_error=True)
#dense_model_name="BAAI/bge-base-en-v1.5"

pipeline = EmbeddingPipeline(collection_name="biomedical_entity_collection_v2.0")
pipeline.add_documents(entities, batch_size=144)

ray.shutdown()

2025-04-03 20:44:22,230	INFO worker.py:1843 -- Started a local Ray instance. View the dashboard at http://127.0.0.1:8265 


Creating embedding workers...
Initializing Qdrant client...
No existing upload log found, starting fresh
Creating new collection 'biomedical_entity_collection_v2.0'
Collection initialized successfully
Adding 2650724 documents in batches of 144
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 3.327388048171997 seconds
Creating points...
Uploading points...
✓ Batch 1/18408 - Total uploaded: 144
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 3.510406255722046 seconds
Creating points...
Uploading points...
✓ Batch 2/18408 - Total uploaded: 288
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 2.800842046737671 seconds
Creating points...
Uploading points...
✓ Batch 3/18408 - Total uploaded: 432
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 2.451000928878784 seconds
Creating points...
Uploading points...
✓ Batch 4/18408 - Total uploaded: 

(raylet) [2025-04-04 00:53:48,272 E 18579 63310] (raylet) file_system_monitor.cc:116: /tmp/ray/session_2025-04-03_20-44-21_203983_15686 is over 95% full, available space: 23.0143 GB; capacity: 460.432 GB. Object creation will fail if spilling is required.


Time taken to generate dense embeddings with Ray Distributed Computing: 0.9219026565551758 seconds
Creating points...
Uploading points...
✓ Batch 8659/18408 - Total uploaded: 1246896
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 1.0900771617889404 seconds
Creating points...
Uploading points...
✓ Batch 8660/18408 - Total uploaded: 1247040
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 1.028090000152588 seconds
Creating points...
Uploading points...
✓ Batch 8661/18408 - Total uploaded: 1247184
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 0.8927249908447266 seconds
Creating points...
Uploading points...
✓ Batch 8662/18408 - Total uploaded: 1247328
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 0.8613641262054443 seconds
Creating points...
Uploading points...
✓ Batch 8663/18408 - Total uploaded: 1247472
Chunk size: 36


(raylet) [2025-04-04 00:53:58,368 E 18579 63310] (raylet) file_system_monitor.cc:116: /tmp/ray/session_2025-04-03_20-44-21_203983_15686 is over 95% full, available space: 22.9055 GB; capacity: 460.432 GB. Object creation will fail if spilling is required.


...

Time taken to generate dense embeddings with Ray Distributed Computing: 0.7926452159881592 seconds
Creating points...
Uploading points...
✓ Batch 9392/18408 - Total uploaded: 1352448
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 0.6956641674041748 seconds
Creating points...
Uploading points...
✓ Batch 9393/18408 - Total uploaded: 1352592
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 0.6949713230133057 seconds
Creating points...
Uploading points...
✓ Batch 9394/18408 - Total uploaded: 1352736
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 0.6842739582061768 seconds
Creating points...
Uploading points...
✓ Batch 9395/18408 - Total uploaded: 1352880
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 0.7314310073852539 seconds
Creating points...
Uploading points...
✓ Batch 9396/18408 - Total uploaded: 1353024
Chunk size: 36
Time taken

(raylet) [2025-04-04 01:14:04,328 E 18579 63310] (raylet) file_system_monitor.cc:116: /tmp/ray/session_2025-04-03_20-44-21_203983_15686 is over 95% full, available space: 20.8658 GB; capacity: 460.432 GB. Object creation will fail if spilling is required.


Time taken to generate dense embeddings with Ray Distributed Computing: 1.2978050708770752 seconds
Creating points...
Uploading points...
✓ Batch 9399/18408 - Total uploaded: 1353456
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 1.0202839374542236 seconds
Creating points...
Uploading points...
✓ Batch 9400/18408 - Total uploaded: 1353600
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 0.9939970970153809 seconds
Creating points...
Uploading points...
✓ Batch 9401/18408 - Total uploaded: 1353744
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 1.0899131298065186 seconds
Creating points...
Uploading points...
✓ Batch 9402/18408 - Total uploaded: 1353888
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 1.0075037479400635 seconds
Creating points...
Uploading points...
✓ Batch 9403/18408 - Total uploaded: 1354032
Chunk size: 36
Time taken

2025-04-04 01:33:02,538	INFO worker.py:1843 -- Started a local Ray instance. View the dashboard at http://127.0.0.1:8265 


Initialized Ray again and recreated embedding workers...
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 12.307528018951416 seconds
Creating points...
Uploading points...
✓ Batch 10001/18408 - Total uploaded: 1440144
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 0.6881096363067627 seconds
Creating points...
Uploading points...
✓ Batch 10002/18408 - Total uploaded: 1440288
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 0.6563320159912109 seconds
Creating points...
Uploading points...
✓ Batch 10003/18408 - Total uploaded: 1440432
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 0.6345021724700928 seconds
Creating points...
Uploading points...
✓ Batch 10004/18408 - Total uploaded: 1440576
Chunk size: 36
Time taken to generate dense embeddings with Ray Distributed Computing: 0.6651368141174316 seconds
Creating points...
Uploading poin

In [4]:
import ray

ray.shutdown()